<font color="firebrick" size="6"><b>selenium(old version)</b></font>


<font color="Maroon" size="5"><b>키워드 정리 Test</b></font>

## API 키워드 전처리

In [ ]:
import pandas as pd
import numpy as np

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
%cd /content/drive/MyDrive/크롤링/키워드 분석

In [ ]:
!pwd

In [ ]:
!ls

In [ ]:
category1 = pd.read_excel("/content/drive/MyDrive/크롤링/키워드 분석/Category0_search.xlsx",sheet_name="카테고리 항목들 수집",header=None)

In [ ]:
category1.to_csv("/content/drive/MyDrive/크롤링/키워드 분석/Category0_search.csv")

In [ ]:
category1 = pd.read_csv("/content/drive/MyDrive/크롤링/키워드 분석/Category0_search.csv").T
category1.drop("Unnamed: 0", axis = 0 ,inplace =True)

In [ ]:
lsts = category1.iloc[0].to_numpy()  # Series를 numpy array 변환
fixed_len = 5-len(lsts) % 5 # 5열을 맞추기 위해 남는 수 유추
lsts = np.pad(lsts,(0,fixed_len),'constant',constant_values=None) # API 키워드 넣을때 ? : 5 shape 맞추기 위한 전처리
new_lsts = lsts.reshape(-1,5)
new_lsts

In [ ]:
new_lsts.shape

## 네이버 API

In [ ]:
# test cell
import time
import requests
import signaturehelper

def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

uri = '/keywordstool'
method = 'GET'
query = {
    "siteId" : "",
    "biztpId" : "",
    "hintKeywords":   new_lsts[0],
    "event": "",
    "month": "",
    "showDetail": "1"
}
response = requests.get(BASE_URL + uri ,
                        params=query,
                        headers=get_header(
                        method=method,
                        uri=uri,
                        api_key= API_KEY,
                        secret_key= SECRET_KEY,
                        customer_id= CUSTOMER_ID))
r_data = response.json()
keywordList = r_data['keywordList']
main_keywordList = keywordList[:5]

for idx,key in enumerate(main_keywordList):
    pcCnt = key["monthlyPcQcCnt"]
    mobileCnt = key["monthlyMobileQcCnt"]

    print(f"Pc 검색량 : {pcCnt}  \t  Mobile 검색량 : {mobileCnt}")



In [ ]:
# 키워드 분석_version(1.0.2)
import time
import requests
import signaturehelper
from bs4 import BeautifulSoup
import openpyxl


def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

cnt = 0
n_cnt = 0

# 네이버 API
for idx,new_lst in enumerate(new_lsts):
    uri = '/keywordstool'
    method = 'GET'
    query = {
        "siteId" : "",
        "biztpId" : "",
        "hintKeywords": new_lst,
        "event": "",
        "month": "",
        "showDetail": "1"
    }
    response_api = requests.get(BASE_URL + uri ,
                            params=query,
                            headers=get_header(
                                method=method,
                                uri=uri,
                                api_key= API_KEY,
                                secret_key= SECRET_KEY,
                                customer_id= CUSTOMER_ID))
    r_data = response_api.json()
    keywordList = r_data['keywordList']
    main_keywordList = keywordList[:5]

    for idx,key in enumerate(main_keywordList):

        # 쇼핑몰 스토어 수
        url = f"https://search.shopping.naver.com/search/all?query={key['relKeyword']}%20%20%09%20%20&frm=NVSHSRC&vertical=search"
        response_shopping = requests.get(url, headers={"User-Agent":"Mozilla/5.0"})
        html = response_shopping.text
        soup = BeautifulSoup(html,"html.parser")
        total_num = soup.select(".subFilter_num__S9sle")[0].text.replace(",","")

        try :
            pcCnt = float(key["monthlyPcQcCnt"])
            mobileCnt = float(key["monthlyMobileQcCnt"])
            totalCnt = pcCnt + mobileCnt
            print(f"관련 키워드 : {key['relKeyword']}  \t  총 검색량 : {totalCnt} \t  총 스토어 수 {total_num}")
            cnt += 1
        except :
            print("검색량 10개 이하")
            n_cnt += 1

print(f"count : {cnt}  |  Uncount : {n_cnt}")


# print("관련 키: ", keywordList[0]['relKeyword'] )
# print("월간 검색수_PC: ",keywordList[0]['monthlyPcQcCnt'] )
# print("월간 검색수_Mobile: ",keywordList[0]['monthlyMobileQcCnt'] )
# print("월 평균 클릭수_PC: ",keywordList[0]['monthlyAvePcClkCnt'] )
# print("월 평균 클릭수_Mobile",keywordList[0]['monthlyAveMobileClkCnt'] )
# print("월 평균 클릭률_PC: ",keywordList[0]['monthlyAvePcCtr'] )
# print("월 평균 클릭수_Mobile: ",keywordList[0]['monthlyAveMobileCtr'] )
# print("경쟁정도: ",keywordList[0]['plAvgDepth'] )
# print("월평균 노출 광고수: ",keywordList[0]['compIdx'] )

In [ ]:
# 키워드 분석_version(1.0.3)
import time
import requests
import signaturehelper
from bs4 import BeautifulSoup
import openpyxl
from tqdm import tqdm


def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

cnt = 0
n_cnt = 0

# 네이버 API

analysis_data = pd.DataFrame(columns=["relative_keyword","total_search","total_store_count","competitive_rate"])
for idx,new_lst in tqdm(enumerate(new_lsts)):
    uri = '/keywordstool'
    method = 'GET'
    query = {
        "siteId" : "",
        "biztpId" : "",
        "hintKeywords": new_lst,
        "event": "",
        "month": "",
        "showDetail": "1"
    }
    response_api = requests.get(BASE_URL + uri ,
                            params=query,
                            headers=get_header(
                                method=method,
                                uri=uri,
                                api_key= API_KEY,
                                secret_key= SECRET_KEY,
                                customer_id= CUSTOMER_ID))
    r_data = response_api.json()
    keywordList = r_data['keywordList']
    main_keywordList = keywordList[:5]

    for idx,key in enumerate(main_keywordList):

        # 쇼핑몰 스토어 수
        url = f"https://search.shopping.naver.com/search/all?query={key['relKeyword']}%20%20%09%20%20&frm=NVSHSRC&vertical=search"
        response_shopping = requests.get(url, headers={"User-Agent":"Mozilla/5.0"})
        html = response_shopping.text
        soup = BeautifulSoup(html,"html.parser")
        total_num = float(soup.select(".subFilter_num__S9sle")[0].text.replace(",",""))

        try :
            pcCnt = float(key["monthlyPcQcCnt"])
            mobileCnt = float(key["monthlyMobileQcCnt"])
            totalCnt = pcCnt + mobileCnt
            competive_rate = np.around(total_num/totalCnt,2)

            # DataFrame 형태 만들기
            tmp = pd.DataFrame({"relative_keyword":[key['relKeyword']],"total_search":[totalCnt],"total_store_count":[total_num],"competitive_rate":[competive_rate]})
            analysis_data = pd.concat([analysis_data,tmp],axis=0)
            # print(f"관련 키워드 : {key['relKeyword']}  \t  총 검색량 : {totalCnt} \t  총 스토어 수 {total_num}")
            cnt += 1
        except :
            n_cnt += 1

print(f"\ncount : {cnt}  |  Uncount : {n_cnt}")


# print("관련 키: ", keywordList[0]['relKeyword'] )
# print("월간 검색수_PC: ",keywordList[0]['monthlyPcQcCnt'] )
# print("월간 검색수_Mobile: ",keywordList[0]['monthlyMobileQcCnt'] )
# print("월 평균 클릭수_PC: ",keywordList[0]['monthlyAvePcClkCnt'] )
# print("월 평균 클릭수_Mobile",keywordList[0]['monthlyAveMobileClkCnt'] )
# print("월 평균 클릭률_PC: ",keywordList[0]['monthlyAvePcCtr'] )
# print("월 평균 클릭수_Mobile: ",keywordList[0]['monthlyAveMobileCtr'] )
# print("경쟁정도: ",keywordList[0]['plAvgDepth'] )
# print("월평균 노출 광고수: ",keywordList[0]['compIdx'] )

In [ ]:
analysis_data.index = np.arange(1,analysis_data.shape[0]+1)
analysis_data

<font color="Maroon" size="5"><b>대표 키워드 정리</b></font>

## 모든 category 엑셀 합치고 전처리

In [ ]:
import pandas as pd
import numpy as np

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

In [ ]:
%ls

In [ ]:
# category 모두 불러오고 csv 파일 만들기
for i in range(12):
  #globals()는 파이썬 내장 함수로, 현재 전역 심볼 테이블을 나타내는 딕셔너리를 반환
  globals()[f"category{i}"] = pd.read_excel(f"/content/drive/MyDrive/크롤링/네이버쇼핑몰크롤링/Category{i}_search.xlsx",sheet_name="카테고리 항목들 수집",header=None)
  globals()[f"category{i}"].to_csv(f"/content/drive/MyDrive/크롤링/네이버쇼핑몰크롤링/Category{i}_search.csv")

In [ ]:
# category들 전처리
for i in range(12):
  globals()[f"category{i}"] = pd.read_csv(f"/content/drive/MyDrive/크롤링/네이버쇼핑몰크롤링/Category{i}_search.csv").T
  globals()[f"category{i}"].drop("Unnamed: 0", axis = 0 ,inplace =True)

In [ ]:
lsts = np.array([])
for i in range(12):
  tmp = globals()[f"category{i}"].iloc[0].to_numpy()  # Series를 numpy array 변환
  lsts = np.concatenate((lsts,tmp))

In [ ]:
# 띄어쓰기 and "/" 제외  -> 제외 안하면 검색 할 떄 invalid 뜸
fixed_lsts = []
for lst in lsts :
  items = lst.split('/')
  item  = [item.replace(" ","") for item in items]
  fixed_lsts.extend(item)
fixed_lsts = np.array(fixed_lsts)
fixed_lsts.shape


In [ ]:
fixed_len = 5-len(lsts) % 5 # 5열을 맞추기 위해 남는 수 유추
new_lsts = np.pad(fixed_lsts,(0,fixed_len),'constant',constant_values=None) # API 키워드 넣을때 ? : 5 shape 맞추기 위한 전처리
new_lsts.shape

In [ ]:
new_lsts = new_lsts.reshape(-1,5)
new_lsts.shape

In [ ]:
pd.set_option('display.max_rows',None)
pd.DataFrame(new_lsts)

In [ ]:
# 키워드 분석_version(1.2.0)
import time
import requests
import signaturehelper
from bs4 import BeautifulSoup
import openpyxl
from tqdm import tqdm


def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

cnt = 0
n_cnt = 0

# 네이버 API

analysis_data = pd.DataFrame(columns=["relative_keyword","total_search","total_store_count","competitive_rate"])
for idx, new_lst in enumerate(new_lsts):
    print(f"\n{idx} : ",end=" ")
    uri = '/keywordstool'
    method = 'GET'
    query = {
        "siteId" : "",
        "biztpId" : "",
        "hintKeywords": new_lst,
        "event": "",
        "month": "",
        "showDetail": "1"
    }
    response_api = requests.get(BASE_URL + uri ,
                            params=query,
                            headers=get_header(
                                method=method,
                                uri=uri,
                                api_key= API_KEY,
                                secret_key= SECRET_KEY,
                                customer_id= CUSTOMER_ID))
    try:   # 처음 try는 키워드의 invaild 또는 스토어 수 requests 에 실패 대응
      r_data = response_api.json()
      keywordList = r_data['keywordList']
      main_keywordList = keywordList[:5]

      for key_idx,key in enumerate(main_keywordList):

          # 쇼핑몰 스토어 수
          url = f"https://search.shopping.naver.com/search/all?query={key['relKeyword']}%20%20%09%20%20&frm=NVSHSRC&vertical=search"
          response_shopping = requests.get(url, headers={"User-Agent":"Mozilla/5.0"})
          html = response_shopping.text
          soup = BeautifulSoup(html,"html.parser")
          total_num = float(soup.select(".subFilter_num__S9sle")[0].text.replace(",",""))

          try :
              pcCnt = float(key["monthlyPcQcCnt"])
              mobileCnt = float(key["monthlyMobileQcCnt"])
              totalCnt = pcCnt + mobileCnt
              competive_rate = np.around(total_num/totalCnt,2)

              # DataFrame 형태 만들기
              tmp = pd.DataFrame({"relative_keyword":[key['relKeyword']],"total_search":[totalCnt],"total_store_count":[total_num],"competitive_rate":[competive_rate]})
              analysis_data = pd.concat([analysis_data,tmp],axis=0)
              # print(f"관련 키워드 : {key['relKeyword']}  \t  총 검색량 : {totalCnt} \t  총 스토어 수 {total_num}")
              cnt += 1
              print(".", end= "")
          except :
            # 검색량 10개 이하 경우 생략
              print(":", end= "")
              n_cnt += 1

    except :
      for i in range(key_idx,5) :  #  key_idx를 확인해서 문제 있는 부분 부터 다시 시도
        try :
          query = {
                "siteId" : "",
                "biztpId" : "",
                "hintKeywords":   new_lst[i],
                "event": "",
                "month": "",
                "showDetail": "1"}

          response = requests.get(BASE_URL + uri ,
                        params=query,
                        headers=get_header(
                        method=method,
                        uri=uri,
                        api_key= API_KEY,
                        secret_key= SECRET_KEY,
                        customer_id= CUSTOMER_ID))

          r_data = response.json()
          keywordList = r_data['keywordList']
          main_keywordList = keywordList[0]

          # 쇼핑몰 스토어 수
          url = f"https://search.shopping.naver.com/search/all?query={main_keywordList['relKeyword']}%20%20%09%20%20&frm=NVSHSRC&vertical=search"
          response_shopping = requests.get(url, headers={"User-Agent":"Mozilla/5.0"})
          html = response_shopping.text
          soup = BeautifulSoup(html,"html.parser")
          total_num = float(soup.select(".subFilter_num__S9sle")[0].text.replace(",",""))


          try :  # 문제있는 부분부터 다시 시작해서 10개 이하 필터링
            pcCnt = float(main_keywordList["monthlyPcQcCnt"])
            mobileCnt = float(main_keywordList["monthlyMobileQcCnt"])
            totalCnt = pcCnt + mobileCnt
            competive_rate = np.around(total_num/totalCnt,2)
            tmp = pd.DataFrame({"relative_keyword":[main_keywordList['relKeyword']],"total_search":[totalCnt],"total_store_count":[total_num],"competitive_rate":[competive_rate]})
            analysis_data = pd.concat([analysis_data,tmp],axis=0)
            cnt += 1
            print(",",end="")
          except :
              print(":",end="")
              n_cnt += 1

        except  IndexError as e:  # 문제 있는 부분은 쇼핑에 "도서" 부분으로 데이터 수집 제외
          print(" 도서 책 제외 ", end= "")
          n_cnt += 1

print(f"\nCOUNT : {cnt}  |  UNCOUNT : {n_cnt}")


In [ ]:
analysis_data.to_csv("대표카테고리_키워드정리.csv", index=False)

In [ ]:
analysis_data.index = np.arange(1,len(analysis_data)+1)
analysis_data.shape

In [ ]:
pd.set_option('display.max_row', None)
analysis_data[analysis_data["competitive_rate"]< 3]

<font color="firebrick" size="6"><b>cid_requests (new version)</b></font>

<font color="Maroon" size="5"><b>대표 키워드 정리</b></font>

In [1]:
import pandas as pd 
import numpy as np
import os
import time
import requests
from bs4 import BeautifulSoup
import openpyxl
import json

In [4]:
os.chdir("../../../smartstore") # signaturehelper module 호출하기 위해 경로 설정
from naverDataLab import signaturehelper

In [ ]:
#  상위 폴더의 signaturehelper 호출은 위한 sys.path 설정
import sys
sys.path.append(os.path.dirname(os.path.abspath(os.getcwd())))

In [5]:
print(os.getcwd())

C:\Users\kcjer\smartstore


In [6]:
os.path.abspath(os.getcwd())

'C:\\Users\\kcjer\\smartstore'

In [ ]:
cid_keywords = pd.read_csv("primaryCategoryDate/231206_cid_keyword/category_search_top20_231206.csv", index_col=False)
cid_keywords

In [ ]:
# 네이버API keyword에 넣기 위해 keyword만 추출
keywords = cid_keywords.iloc[:,2:]
keywords

In [ ]:
# 네이버API keyword에 넣기 위해 ravel하고  N : 5 의 shape형태로 맞춤
ravel_keywords = keywords.values.ravel()
ravel_keywords = ravel_keywords.reshape(-1,5)
ravel_keywords.shape

In [ ]:
# pd.set_option('display.max_rows',None)
# pd.DataFrame(ravel_keywords)

In [ ]:
product_cookies = {
    'NNB': 'C7EDCEISD3PWE',
    'ASID': '75100b2b0000018238f7a1dd00000069',
    'autocomplete': 'use',
    'AD_SHP_BID': '3',
    '_ga': 'GA1.2.1844324501.1673338909',
    'SHP_BUCKET_ID': '5',
    'NaverSuggestUse': 'unuse%26use',
    'nx_ssl': '2',
    'nid_inf': '816806566',
    'NID_AUT': 'VGdlDpncPMjmAYb3n77vxEbA3RQrgxnItTHmknLCZh0IV2uMH+6NEuJSE0cI4rBS',
    'NID_JKL': 'DGP6mtx85jwbG9AZKkD1IvLoc9F3QrAjT+Bl3xbZrMM=',
    'ncpa': '188760|lpuye2g8|346dbd05dc88ff23ce38ac47ab0894d1fe0f6ec6|s_1f0bdf2d3b2c|6b94cc54608c09858c61f2a6c8471382631a8ab8',
    'NID_SES': 'AAABgE9XswZYIx6gOsXCYcwfnLTVtAkzFzmKbVT2EgLy++hE0Y5G3f8zQ3qBt03DysXE2NXzaUZIdJ6a6DDYDjPmG0huOT4Tcl6+Cei63abC4raW3FwlEsfw3mphmiDUSPzLnWBMGuekMXe6vQHJZ5W4UH0P9HI0WW50FTNpeX3nH/JNmmV2oIYTVyg8X4hX9YZLxVZ/2wqOvULOOZHwGmg4wx7OtxxKCUr6J88s3+YrgcRLZpJvobPfHB/Nb/Q6+IkGmPXUqCZBTReubye8UBLpZlwU4jxkslrvimhFuL0aADRYqAf6Q9rTJRRjHdrLK6afwjR2oEVQGBzJXZgSJZcr5+EH42/95IkU73Z026HgS63IoWWHlFCQuG+gXaU6yL2c1cYJVQybcYmfbDbbQMCigC0XxQJiD/xvpjdNyg3yAXVPfZH1PRcIr8etGqz9VHOZ8sm6ObAeI1AlPL0w8y7Gq+8UHdcPi2x8QRoqtvbjWVAK+Er8OM2pGX3ni7PAiIQtbA==',
    'page_uid': 'iUbPiwqVOsossbnI51Zssssstyl-212228',
    'spage_uid': 'iUbPiwqVOsossbnI51Zssssstyl-212228',
}

product_headers = {
    'authority': 'search.shopping.naver.com',
    'accept': 'application/json, text/plain, */*',
    'accept-language': 'ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7',
    # 'cookie': 'NNB=C7EDCEISD3PWE; ASID=75100b2b0000018238f7a1dd00000069; autocomplete=use; AD_SHP_BID=3; _ga=GA1.2.1844324501.1673338909; SHP_BUCKET_ID=5; NaverSuggestUse=unuse%26use; nx_ssl=2; nid_inf=816806566; NID_AUT=VGdlDpncPMjmAYb3n77vxEbA3RQrgxnItTHmknLCZh0IV2uMH+6NEuJSE0cI4rBS; NID_JKL=DGP6mtx85jwbG9AZKkD1IvLoc9F3QrAjT+Bl3xbZrMM=; ncpa=188760|lpuye2g8|346dbd05dc88ff23ce38ac47ab0894d1fe0f6ec6|s_1f0bdf2d3b2c|6b94cc54608c09858c61f2a6c8471382631a8ab8; NID_SES=AAABgE9XswZYIx6gOsXCYcwfnLTVtAkzFzmKbVT2EgLy++hE0Y5G3f8zQ3qBt03DysXE2NXzaUZIdJ6a6DDYDjPmG0huOT4Tcl6+Cei63abC4raW3FwlEsfw3mphmiDUSPzLnWBMGuekMXe6vQHJZ5W4UH0P9HI0WW50FTNpeX3nH/JNmmV2oIYTVyg8X4hX9YZLxVZ/2wqOvULOOZHwGmg4wx7OtxxKCUr6J88s3+YrgcRLZpJvobPfHB/Nb/Q6+IkGmPXUqCZBTReubye8UBLpZlwU4jxkslrvimhFuL0aADRYqAf6Q9rTJRRjHdrLK6afwjR2oEVQGBzJXZgSJZcr5+EH42/95IkU73Z026HgS63IoWWHlFCQuG+gXaU6yL2c1cYJVQybcYmfbDbbQMCigC0XxQJiD/xvpjdNyg3yAXVPfZH1PRcIr8etGqz9VHOZ8sm6ObAeI1AlPL0w8y7Gq+8UHdcPi2x8QRoqtvbjWVAK+Er8OM2pGX3ni7PAiIQtbA==; page_uid=iUbPiwqVOsossbnI51Zssssstyl-212228; spage_uid=iUbPiwqVOsossbnI51Zssssstyl-212228',
    'logic': 'PART',
    'referer': 'https://search.shopping.naver.com/search/all?query=%EC%BC%80%EC%9D%B4%EC%8A%A4%20%20%09%20%20&frm=NVSHSRC&vertical=search',
    'sbth': 'e45d2ed3a9d626f086dd5b7c959f1653ebf418dda3b68d03f388890946c54c13792df120f202cfda5512927c08d13e6d',
    'sec-ch-ua': '"Google Chrome";v="119", "Chromium";v="119", "Not?A_Brand";v="24"',
    'sec-ch-ua-arch': '"x86"',
    'sec-ch-ua-bitness': '"64"',
    'sec-ch-ua-full-version-list': '"Google Chrome";v="119.0.6045.200", "Chromium";v="119.0.6045.200", "Not?A_Brand";v="24.0.0.0"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-model': '""',
    'sec-ch-ua-platform': '"Windows"',
    'sec-ch-ua-platform-version': '"10.0.0"',
    'sec-ch-ua-wow64': '?0',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-origin',
    'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36',
}

In [ ]:
# # 데이터프레임 (처음 세팅)
# analysis_data = pd.DataFrame(columns=["relative_keyword","total_search","total_store_count","competitive_rate"])
# unanalysis_data = pd.DataFrame(columns=["relative_keyword","total_search"])

# analysis_data.to_csv("conditionedData/data/data_231206/1_primary/1_primary.csv", index=False)
# unanalysis_data.to_csv("conditionedData/data/data_231206/1_primary/1_primary_deleted_requests.csv", index=False)

In [ ]:
def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

cnt = 0 # 카운트 된 수
n_cnt = 0 # 카운트 안된 수
start_idx = 0

# 네이버 API

# 데이터프레임 (중도 세팅)
analysis_data = pd.read_csv("conditionedData/data/data_231206/1_primary/1_primary.csv", index_col=False)
unanalysis_data =  pd.read_csv("conditionedData/data/data_231206/1_primary/1_primary_deleted_requests.csv", index_col=False)

for idx, ravel_keyword in enumerate(ravel_keywords[start_idx:,:]):  #[9:,:]
    print(f"{start_idx+idx} : ", end = " ")
    uri = '/keywordstool'
    method = 'GET'
    query = {
        "siteId" : "",
        "biztpId" : "",
        "hintKeywords": ravel_keyword,
        "event": "",
        "month": "",
        "showDetail": "1"
    }

    response_api = requests.get(BASE_URL + uri ,
                                params=query,
                                headers=get_header(
                                method=method,
                                uri=uri,
                                api_key= API_KEY,
                                secret_key= SECRET_KEY,
                                customer_id= CUSTOMER_ID))

    try :  # Too Many Requests가 뜨는 경우(아주 가끔뜨는데 except으로 넘김)
        r_data = response_api.json()
        keywordList = r_data['keywordList']
        main_keywordList = keywordList[:5]
        
        for key_idx,key in enumerate(main_keywordList):
            try:
                # 모바일 + PC 클릭량 
                pcCnt = float(key["monthlyPcQcCnt"])
                mobileCnt = float(key["monthlyMobileQcCnt"])
                totalCnt = pcCnt + mobileCnt

                try:
                    # 쇼핑몰 스토어 수
                    product_params = {
                        'adQuery': key['relKeyword'],
                        'eq': '',
                        'frm': 'NVSHSRC',
                        'iq': '',
                        'origQuery': key['relKeyword'],
                        'pagingIndex': '1',
                        'pagingSize': '20',
                        'productSet': 'total',
                        'query': key['relKeyword'],
                        'sort': 'rel',
                        'viewType': 'list',
                        'xq': '',
                        }
                    
                    response = requests.get('https://search.shopping.naver.com/api/search/all', params=product_params, cookies=product_cookies, headers=product_headers)
                    product = json.loads(response.text)
                    total_num = product["productSetFilter"]["filterValues"][0]["productCount"]
                    
                    competive_rate = np.around(total_num/totalCnt,2)

                    # DataFrame 형태 만들기
                    tmp = pd.DataFrame({"relative_keyword":[key['relKeyword']],"total_search":[totalCnt],"total_store_count":[total_num],"competitive_rate":[competive_rate]})
                    analysis_data = pd.concat([analysis_data,tmp],axis=0)
                    cnt += 1
                    analysis_data.to_csv("conditionedData/data/data_231206/1_primary/1_primary.csv", index=False)
                    print(f"\tO ", end="") # key['keywordList'][key_idx]['relKeyword']  (키워드명)


                except:        
                    tmp = pd.DataFrame({"relative_keyword":[key['relKeyword']],"total_search":[totalCnt]})
                    unanalysis_data = pd.concat([unanalysis_data,tmp],axis=0)
                    unanalysis_data.to_csv("conditionedData/data/data_231206/1_primary/1_primary_deleted_requests.csv", index=False)
                    print(f"\tX({key['relKeyword']})", end="")
                    n_cnt += 1

            except : 
                print(f"\t10개 이하({key['relKeyword']})", end="")
                n_cnt += 1
                
        print("")
            
    except : 
        print("Too Many Requests")


In [ ]:
data  = pd.read_csv("conditionedData/data/data_231201/1_primary.csv")
data.drop_duplicates(["relative_keyword"],inplace=True)
data.index = np.arange(1,len(data)+1)


<font color="Maroon" size="5"><b>전체 스토어수 (API 오류로 클릭량은 코랩에서 진행)</b></font>

In [7]:
import warnings
warnings.filterwarnings("ignore")

In [ ]:
# # 데이터프레임 (처음 세팅)
# primary_store = pd.DataFrame(columns=["relative_keyword","total_store"])

# primary_store.to_csv("conditionedData/data/data_231206/1_primary/1_primary_total_store.csv", index=False)

In [8]:
pd.set_option('display.max_rows',100)

In [9]:
primary_search = pd.read_csv("conditionedData/data/data_231206/1_primary/1_primary_search.csv", index_col=False)
primary_search

relative_keyword  total_search
0                  크록스      623400.0
1               나이키운동화      285000.0
2                  실내화       57900.0
3                   양말      153100.0
4                  캐리어      241000.0
...                ...           ...
89381           나이키에코백        5590.0
89382           셀린느에코백        8900.0
89383         이자벨마랑에코백        5450.0
89384           아페쎄에코백        9120.0
89385            명품에코백        5010.0

[89386 rows x 2 columns]

In [10]:
# 데이터 전처리
primary_search = primary_search[(primary_search["total_search"]>1000) & (primary_search["total_search"]<30000)]
primary_search.index =  np.arange(len(primary_search["relative_keyword"]))

pd.set_option('display.max_rows',None)
primary_search

relative_keyword  total_search
0                        깔창       21960.0
1                   종아리압박밴드       11230.0
2                     페이크삭스        5210.0
3                      시카크림       25760.0
4                        틴트       21120.0
5                        앰플       19130.0
6                      마사지젤        5230.0
7                     약산성샴푸       14540.0
8                       샴푸바       16920.0
9                      핸드워시       27520.0
10                   유무선공유기        2620.0
11                      복합기       20120.0
12                  블루투스헤드셋       25040.0
13                    사무용의자       29000.0
14                     수납선반       13420.0
15                   어린이마스크       10050.0
16                    유아마스크       12060.0
17                     낮잠이불       18630.0
18                     아기로션       12730.0
19                    소형마스크        4630.0
20                     아기크림        4170.0
21                     아기세제       12170.0
22                어린이집생일답례품       18540.0
23                   결혼식답례품       28110.0
24                   티니핑마스크        9550.0
25                  골프거리측정기       29040.0
26                     캠핑랜턴       17580.0
27                       아령       20980.0
28                     헤드랜턴       23980.0
29                     구명조끼       15700.0
30                   팔꿈치보호대       24490.0
31                     캠핑박스       14760.0
32                  KF94마스크       28860.0
33                    덴탈마스크       25520.0
34              KF94마스크새부리형        6330.0
35                     전담액상       22170.0
36                   발각질제거기       23560.0
37                     축하화환       26400.0
38                     개업화환       13910.0
39                비발디파크리프트권       13580.0
40                     꽃바구니       19770.0
41                    결혼식화환       14460.0
42                     유럽유심       14680.0
43                    캠핑카렌트       21950.0
44                     태국유심       27120.0
45                비발디파크스키강습       22320.0
46                    에어컨청소       13680.0
47                오피신유니버셀불리        4120.0
48                   면세점립스틱        1130.0
49                  꾸셀파운데이션        2370.0
50                      CPB        3180.0
51                꾸셀베이스오리지널        1370.0
52                    면세점향수        4030.0
53                인천공항면세점향수        2670.0
54                   르라보면세점        1060.0
55                 불리목욕하는여인       10550.0
56                  면세점향수추천        1280.0
57                    면세점시계        1080.0
58                    면세점어그        2990.0
59                    어그면세점        2680.0
60                    밍크엘레팡        1960.0
61                    콜드프레임        8340.0
62                  다미아니귀걸이        1380.0
63                    롱샴면세점        2030.0
64                    면세점가방        3110.0
65              인천공항면세점선글라스        1760.0
66                  면세점선글라스        2200.0
67                  면세점가방추천        1100.0
68                    면세점지갑        1130.0
69                인천공항면세점지갑        2100.0
70                   면세점캐리어        1350.0
71                    카메라추천        9010.0
72                     러닝가방        1700.0
73                     런닝벨트        1200.0
74                     러닝벨트        6490.0
75                  스포벨러닝벨트        1020.0
76                     러닝용품        1560.0
77                     당구큐대       11080.0
78                      당구큐        3450.0
79                     당구장갑        3340.0
80                    당구큐가방        1500.0
81                     롱고니큐        2910.0
82                     당구그립        1230.0
83                     카본큐대        1030.0
84                      한밭큐        6100.0
85                      당구팁        2060.0
86                     쿠드롱팁        1050.0
87                       큐대        1640.0
88                    아담무사시        2170.0
89                     무사시큐        2160.0
90                    중고당구대        1710.0
91                   게이트볼스틱        1490.0
92                     승마바지        2600.0
93                   컴파운드보우        4740.0
94                   

In [12]:
pd.set_option('display.max_rows',100)

In [13]:
ravel_keywords = primary_search["relative_keyword"]
ravel_keywords.shape

(40679,)

In [ ]:
product_cookies = {
    'NNB': 'C7EDCEISD3PWE',
    'ASID': '75100b2b0000018238f7a1dd00000069',
    'autocomplete': 'use',
    'AD_SHP_BID': '3',
    '_ga': 'GA1.2.1844324501.1673338909',
    'SHP_BUCKET_ID': '5',
    'NaverSuggestUse': 'unuse%26use',
    'nx_ssl': '2',
    'nid_inf': '816806566',
    'NID_AUT': 'VGdlDpncPMjmAYb3n77vxEbA3RQrgxnItTHmknLCZh0IV2uMH+6NEuJSE0cI4rBS',
    'NID_JKL': 'DGP6mtx85jwbG9AZKkD1IvLoc9F3QrAjT+Bl3xbZrMM=',
    'ncpa': '188760|lpuye2g8|346dbd05dc88ff23ce38ac47ab0894d1fe0f6ec6|s_1f0bdf2d3b2c|6b94cc54608c09858c61f2a6c8471382631a8ab8',
    'NID_SES': 'AAABgE9XswZYIx6gOsXCYcwfnLTVtAkzFzmKbVT2EgLy++hE0Y5G3f8zQ3qBt03DysXE2NXzaUZIdJ6a6DDYDjPmG0huOT4Tcl6+Cei63abC4raW3FwlEsfw3mphmiDUSPzLnWBMGuekMXe6vQHJZ5W4UH0P9HI0WW50FTNpeX3nH/JNmmV2oIYTVyg8X4hX9YZLxVZ/2wqOvULOOZHwGmg4wx7OtxxKCUr6J88s3+YrgcRLZpJvobPfHB/Nb/Q6+IkGmPXUqCZBTReubye8UBLpZlwU4jxkslrvimhFuL0aADRYqAf6Q9rTJRRjHdrLK6afwjR2oEVQGBzJXZgSJZcr5+EH42/95IkU73Z026HgS63IoWWHlFCQuG+gXaU6yL2c1cYJVQybcYmfbDbbQMCigC0XxQJiD/xvpjdNyg3yAXVPfZH1PRcIr8etGqz9VHOZ8sm6ObAeI1AlPL0w8y7Gq+8UHdcPi2x8QRoqtvbjWVAK+Er8OM2pGX3ni7PAiIQtbA==',
    'page_uid': 'iUbPiwqVOsossbnI51Zssssstyl-212228',
    'spage_uid': 'iUbPiwqVOsossbnI51Zssssstyl-212228',
}

product_headers = {
    'authority': 'search.shopping.naver.com',
    'accept': 'application/json, text/plain, */*',
    'accept-language': 'ko-KR,ko;q=0.9,en-US;q=0.8,en;q=0.7',
    # 'cookie': 'NNB=C7EDCEISD3PWE; ASID=75100b2b0000018238f7a1dd00000069; autocomplete=use; AD_SHP_BID=3; _ga=GA1.2.1844324501.1673338909; SHP_BUCKET_ID=5; NaverSuggestUse=unuse%26use; nx_ssl=2; nid_inf=816806566; NID_AUT=VGdlDpncPMjmAYb3n77vxEbA3RQrgxnItTHmknLCZh0IV2uMH+6NEuJSE0cI4rBS; NID_JKL=DGP6mtx85jwbG9AZKkD1IvLoc9F3QrAjT+Bl3xbZrMM=; ncpa=188760|lpuye2g8|346dbd05dc88ff23ce38ac47ab0894d1fe0f6ec6|s_1f0bdf2d3b2c|6b94cc54608c09858c61f2a6c8471382631a8ab8; NID_SES=AAABgE9XswZYIx6gOsXCYcwfnLTVtAkzFzmKbVT2EgLy++hE0Y5G3f8zQ3qBt03DysXE2NXzaUZIdJ6a6DDYDjPmG0huOT4Tcl6+Cei63abC4raW3FwlEsfw3mphmiDUSPzLnWBMGuekMXe6vQHJZ5W4UH0P9HI0WW50FTNpeX3nH/JNmmV2oIYTVyg8X4hX9YZLxVZ/2wqOvULOOZHwGmg4wx7OtxxKCUr6J88s3+YrgcRLZpJvobPfHB/Nb/Q6+IkGmPXUqCZBTReubye8UBLpZlwU4jxkslrvimhFuL0aADRYqAf6Q9rTJRRjHdrLK6afwjR2oEVQGBzJXZgSJZcr5+EH42/95IkU73Z026HgS63IoWWHlFCQuG+gXaU6yL2c1cYJVQybcYmfbDbbQMCigC0XxQJiD/xvpjdNyg3yAXVPfZH1PRcIr8etGqz9VHOZ8sm6ObAeI1AlPL0w8y7Gq+8UHdcPi2x8QRoqtvbjWVAK+Er8OM2pGX3ni7PAiIQtbA==; page_uid=iUbPiwqVOsossbnI51Zssssstyl-212228; spage_uid=iUbPiwqVOsossbnI51Zssssstyl-212228',
    'logic': 'PART',
    'referer': 'https://search.shopping.naver.com/search/all?query=%EC%BC%80%EC%9D%B4%EC%8A%A4%20%20%09%20%20&frm=NVSHSRC&vertical=search',
    'sbth': 'e45d2ed3a9d626f086dd5b7c959f1653ebf418dda3b68d03f388890946c54c13792df120f202cfda5512927c08d13e6d',
    'sec-ch-ua': '"Google Chrome";v="119", "Chromium";v="119", "Not?A_Brand";v="24"',
    'sec-ch-ua-arch': '"x86"',
    'sec-ch-ua-bitness': '"64"',
    'sec-ch-ua-full-version-list': '"Google Chrome";v="119.0.6045.200", "Chromium";v="119.0.6045.200", "Not?A_Brand";v="24.0.0.0"',
    'sec-ch-ua-mobile': '?0',
    'sec-ch-ua-model': '""',
    'sec-ch-ua-platform': '"Windows"',
    'sec-ch-ua-platform-version': '"10.0.0"',
    'sec-ch-ua-wow64': '?0',
    'sec-fetch-dest': 'empty',
    'sec-fetch-mode': 'cors',
    'sec-fetch-site': 'same-origin',
    'user-agent': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36',
}

In [ ]:
start_idx = 21687

primary_store = pd.read_csv("conditionedData/data/data_231206/1_primary/1_primary_total_store.csv")

for idx, ravel_keyword in enumerate(ravel_keywords[start_idx:]):  #[9:,:]\

      # 쇼핑몰 스토어 수
        product_params = {
              'adQuery': ravel_keyword,
              'eq': '',
              'frm': 'NVSHSRC',
              'iq': '',
              'origQuery': ravel_keyword,
              'pagingIndex': '1',
              'pagingSize': '20',
              'productSet': 'total',
              'query': ravel_keyword,
              'sort': 'rel',
              'viewType': 'list',
              'xq': '',
              }
        try:
            response = requests.get('https://search.shopping.naver.com/api/search/all', params=product_params, cookies=product_cookies, headers=product_headers)
            product = json.loads(response.text)
            total_num = product["productSetFilter"]["filterValues"][0]["productCount"]

            time.sleep(np.random.rand()*1.3)

            tmp = pd.DataFrame({"relative_keyword":[ravel_keyword],"total_store":[total_num]})

            primary_store = pd.concat([primary_store,tmp],axis=0)
            primary_store.to_csv("conditionedData/data/data_231206/1_primary/1_primary_total_store.csv", index=False)
            print(f"\t{start_idx} ", end="") # key['keywordList'][key_idx]['relKeyword']  (키워드명)
            start_idx += 1
            
        except:
            tmp = pd.DataFrame({"relative_keyword":[ravel_keyword],"total_store":[None]})
            primary_store = pd.concat([primary_store,tmp],axis=0)
            primary_store.to_csv("conditionedData/data/data_231206/1_primary/1_primary_total_store.csv", index=False)
            print(f"\t*{start_idx}* ", end="") # key['keywordList'][key_idx]['relKeyword']  (키워드명)
            start_idx += 1





<font color="Maroon" size="5"><b>클릭량 + 스토어수 합치기</b></font>

In [14]:
primary_store = pd.read_csv("conditionedData/data/data_231206/1_primary/1_primary_total_store.csv")

In [15]:
pd.set_option('display.max_rows',100)
primary_search.shape , primary_store.shape

((40679, 2), (40679, 2))

In [24]:
primary_store.drop_duplicates(["relative_keyword"],inplace=True)
primary_search.drop_duplicates(["relative_keyword"],inplace=True)

In [25]:
primary_store

relative_keyword  total_store
0                   깔창    1227117.0
1              종아리압박밴드      80106.0
2                페이크삭스     513576.0
3                 시카크림      85425.0
4                   틴트     656807.0
...                ...          ...
40674           나이키에코백       1848.0
40675           셀린느에코백        176.0
40676         이자벨마랑에코백       2034.0
40677           아페쎄에코백      12553.0
40678            명품에코백      39622.0

[31526 rows x 2 columns]

In [26]:
primary_search

relative_keyword  total_search
0                   깔창       21960.0
1              종아리압박밴드       11230.0
2                페이크삭스        5210.0
3                 시카크림       25760.0
4                   틴트       21120.0
...                ...           ...
40674           나이키에코백        5590.0
40675           셀린느에코백        8900.0
40676         이자벨마랑에코백        5450.0
40677           아페쎄에코백        9120.0
40678            명품에코백        5010.0

[31526 rows x 2 columns]

In [28]:
pd.set_option('display.max_rows',100)
data = pd.merge(primary_search, primary_store ,on = 'relative_keyword')
data

relative_keyword  total_search  total_store
0                   깔창       21960.0    1227117.0
1              종아리압박밴드       11230.0      80106.0
2                페이크삭스        5210.0     513576.0
3                 시카크림       25760.0      85425.0
4                   틴트       21120.0     656807.0
...                ...           ...          ...
31521           나이키에코백        5590.0       1848.0
31522           셀린느에코백        8900.0        176.0
31523         이자벨마랑에코백        5450.0       2034.0
31524           아페쎄에코백        9120.0      12553.0
31525            명품에코백        5010.0      39622.0

[31526 rows x 3 columns]

In [29]:
data.to_csv(r"conditionedData/data/data_231206/1_primary/1_primary.csv",index=False)

<font color="Maroon" size="5"><b>Test Cell</b></font>

In [ ]:
# test cell
import time
import requests
from naverDataLab import signaturehelper
from bs4 import BeautifulSoup
import openpyxl


def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.searchad.naver.com'
problem = 4159
main_keywordList = ravel_keywords[problem]

uri = '/keywordstool'
method = 'GET'
query = {
    "siteId" : "",
    "biztpId" : "",
    "hintKeywords":   main_keywordList,
    "event": "",
    "month": "",
    "showDetail": "1"
}
response = requests.get(BASE_URL + uri ,
                        params=query,
                        headers=get_header(
                        method=method,
                        uri=uri,
                        api_key= API_KEY,
                        secret_key= SECRET_KEY,
                        customer_id= CUSTOMER_ID))

try :
    r_data = response.json()
    keywordList = r_data['keywordList']
    main_keywordList = keywordList[:5]
    for idx,key in enumerate(main_keywordList):
        pcCnt = key["monthlyPcQcCnt"]
        mobileCnt = key["monthlyMobileQcCnt"]
        print(f"Pc 검색량 : {pcCnt}  \t  Mobile 검색량 : {mobileCnt}")
        print(f"{key['relKeyword']}")

except:
    for j in range(5) :
#         try :
            main_keywordList =  ravel_keywords[problem][4]
            query = {
                  "siteId" : "",
                  "biztpId" : "",
                  "hintKeywords":   main_keywordList,
                  "event": "",
                  "month": "",
                  "showDetail": "1"}
            
            response = requests.get(BASE_URL + uri ,
                            params=query,
                            headers=get_header(
                            method=method,
                            uri=uri,
                            api_key= API_KEY,
                            secret_key= SECRET_KEY,
                            customer_id= CUSTOMER_ID))
            
            r_data = response.json()
            print(f"{ravel_keywords[problem][j]}")
            print(r_data)
#             keywordList = r_data['keywordList']
#             main_keywordList = keywordList[0]


#             pcCnt = main_keywordList["monthlyPcQcCnt"]
#             mobileCnt = main_keywordList["monthlyMobileQcCnt"]
#             print(f"Pc 검색량 : {pcCnt}  \t  Mobile 검색량 : {mobileCnt}")

#         except  Exception as ex:
#             print(ex)
#             print('There are invalid parameters')








In [ ]:
# test cell
import time
import requests
import signaturehelper

def get_header(method, uri, api_key, secret_key, customer_id):
    timestamp = str(round(time.time() * 1000))
    signature = signaturehelper.Signature.generate(timestamp, method, uri, SECRET_KEY)
    return {'Content-Type': 'application/json; charset=UTF-8',
            'X-Timestamp': timestamp,
            'X-API-KEY': API_KEY,
            'X-Customer': str(CUSTOMER_ID),
            'X-Signature': signature}

API_KEY = '01000000004031c42277f90c7fdcbd2130a4916b0aecf181b89b3543abab0f90b463c42821'
SECRET_KEY = 'AQAAAABAMcQid/kMf9y9ITCkkWsKnGbFkehYuYSpmb3ygOH/tg=='
CUSTOMER_ID = '3003237'
BASE_URL =  'https://api.naver.com'

uri = '/keywordstool'
method = 'GET'
query = {
    "siteId" : "",
    "biztpId" : "",
    "hintKeywords":  "None",
    "event": "",
    "month": "",
    "showDetail": "1"
}
response = requests.get(BASE_URL + uri ,
                        params=query,
                        headers=get_header(
                        method=method,
                        uri=uri,
                        api_key= API_KEY,
                        secret_key= SECRET_KEY,
                        customer_id= CUSTOMER_ID))
r_data = response.json()
print(r_data)


https://developers.naver.com/docs/serviceapi/datalab/shopping/shopping.md#%EC%87%BC%ED%95%91%EC%9D%B8%EC%82%AC%EC%9D%B4%ED%8A%B8-%EA%B0%9C%EC%9A%94